# Computer Vision 🤗

In [1]:
import pandas as pd
import requests
from together import Together
import os
import cv2
import numpy as np
from dotenv import load_dotenv

In [2]:
df = pd.read_excel('bookInfo.xlsx')

In [1]:
from diffusers import DiffusionPipeline
import torch

In [ ]:
# load both base & refiner
base = DiffusionPipeline.from_pretrained(
    "stabilityai/stable-diffusion-xl-base-1.0", torch_dtype=torch.float16, variant="fp16", use_safetensors=True
)
# base.to("cuda")
refiner = DiffusionPipeline.from_pretrained(
    "stabilityai/stable-diffusion-xl-refiner-1.0",
    text_encoder_2=base.text_encoder_2,
    vae=base.vae,
    torch_dtype=torch.float16,
    use_safetensors=True,
    variant="fp16",
)
# refiner.to("cuda")

In [ ]:
# Define how many steps and what % of steps to be run on each experts (80/20) here
n_steps = 40
high_noise_frac = 0.8

prompt = f"Depict a picture based on the summary of a book which will come in the following: {dataframe[0]}"

run both experts
image = base(
    prompt=prompt,
    num_inference_steps=n_steps,
    denoising_end=high_noise_frac,
    output_type="latent",
).images
image = refiner(
    prompt=prompt,
    num_inference_steps=n_steps,
    denoising_start=high_noise_frac,
    image=image,
).images[0]


In [3]:
clipdrop_api = '9cc68d53a32cdecabd28618baaf867d1b2bfd376abbb23787c10ddb31a10d7eefd44a5a6dd77b63debc7cca0f926e370'

In [4]:
random_summary =  df['summary'].sample().iloc[0]

In [5]:
# Load environment variables from .env file
load_dotenv()

# Create client
client = Together(api_key=os.environ.get("TOGETHER_API_KEY"))


response = client.chat.completions.create(
    model="meta-llama/Llama-3-8b-chat-hf",
    messages=[{"role": "user", "content": f"Condense the provided book summary into a concise 900-word limit without adding any extra information like 'Here is the condensed summary within the 900-word limit'.: {random_summary}"}]
)
condense_summary  = response.choices[0].message.content



In [6]:
condense_summary

'A former astronaut is hired by a detective agency to investigate a series of mysterious deaths in Naples spas. The victims, all on vacation, suddenly became mad and committed suicide without apparent reason. The case is initially thought to be a serial murder by poisoning, but the connection between the victims remains unclear.\n\nAs the investigation unfolds, it becomes apparent that certain innocent chemicals can be combined to create a powerful depressant, a type of chemical weapon. The hero, a former astronaut, experiences the effects of the chemical but uses his training to survive and ultimately solve the case.\n\nThrough his investigation, the hero discovers the industrial sources of the chemicals and reveals how random chance chemical reactions led to the string of deaths.'

In [7]:
# Depict a picture based on following summary : {condense_summary}
r = requests.post('https://clipdrop-api.co/text-to-image/v1',
  files = {
      'prompt': (None, f'Depict a picture based on following summary : {condense_summary}', 'text/plain')
  },
  headers = { 'x-api-key': clipdrop_api}
)
# if (r.ok):
# # r.content contains the bytes of the returned image
# else:
#   r.raise_for_status()

In [14]:
r.content

b'\x89PNG\r\n\x1a\n\x00\x00\x00\rIHDR\x00\x00\x04\x00\x00\x00\x04\x00\x08\x02\x00\x00\x00\xf0\x7f\xbc\xd4\x00\x00A\xe1caBX\x00\x00A\xe1jumb\x00\x00\x00\x1ejumdc2pa\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa\x00\x00\x00A\xbbjumb\x00\x00\x00Gjumdc2ma\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03urn:uuid:f10a340d-e9c2-4dd7-a2bc-14901ac8661c\x00\x00\x00\x03%jumb\x00\x00\x00)jumdc2as\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.assertions\x00\x00\x00\x00\xbbjumb\x00\x00\x00)jumdcbor\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x03c2pa.ingredient\x00\x00\x00\x00\x8acbor\xa4hdc:titled.pngidc:formatx\x18application/octet-streamjinstanceIDx,xmp:iid:cc6bf9f3-6233-4f96-a2c4-012f11a67d0blrelationshiphparentOf\x00\x00\x00\xffjumb\x00\x00\x00Njumdjson\x00\x11\x00\x10\x80\x00\x00\xaa\x008\x9bq\x13stds.schema-org.CreativeWork\x00\x00\x00\x00\x18c2shQ\x90\x8c\x14\x95\xfc^\xae\xb6\xfb\xb4L\x0e^\xf0\xa5\x00\x00\x00\xa9json{"@context":"https://schema.org","@type":"CreativeWork","datePublished":"2

In [8]:
byte_array = np.frombuffer(r.content, dtype=np.uint8)

In [9]:
image = cv2.imdecode(byte_array, cv2.IMREAD_COLOR)

In [10]:
cv2.imshow('Image', image)
while True:
    if cv2.waitKey(1) & 0xFF == ord('q'):  # Wait for 'q' key to be pressed
        break
cv2.destroyAllWindows()